In [1]:
# On importe les librairies dont on aura besoin pour la Question2
from sklearn import tree
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import graphviz
from sklearn.tree import DecisionTreeClassifier
from sklearn.tree.export import export_text
from sklearn import tree
from sklearn import metrics
from sklearn.metrics import classification_report
from sklearn.model_selection import learning_curve
from pylab import *

In [2]:
# On charge le dataset d'entrainement et de test
Training_Set = pd.read_csv('../Data/Adult_train.csv', sep=',')
Testing_Set = pd.read_csv('../Data/Adult_test.csv', sep=',')

In [3]:
##__traitement des donnee__##

#on extrait les features des 2 dataset 
X_Training =  Training_Set.drop(['salary'],axis=1)
X_Testing =  Testing_Set.drop(['salary'],axis=1)

# on extrait les étiquettes de classe de l'échantillon d'apprentissage
Y_Training = Training_Set['salary']
Y_Testing = Testing_Set['salary']

#on extrait le nom des features pour remplacer les numero par leur nom respective dans le graphe de l'abre
names_features=[]
with open ("../Data/Adult_train.csv", "r") as f: # ouverture du fichier en mode lecture
    names_features = f.readline().strip().split(",")  # on enlève les caractères de fin de ligne et on découpe en colonnes

#on supprime le dernier nom 'salary' de la liste des noms
del names_features[len(names_features) -1]

In [4]:
##__Construction d'un modèle d'arbre de décision__##

#entrenement de l'abre avec une nodes=3
decision_tree_nodes = DecisionTreeClassifier(random_state=0, max_features=15, criterion="entropy")
decision_tree_nodes = decision_tree_nodes.fit(X_Training, Y_Training)

#entrenement de l'abre avec une profondeur=3
decision_tree_depth = DecisionTreeClassifier(random_state=0, max_depth=3, criterion="entropy")
decision_tree_depth = decision_tree_depth.fit(X_Training, Y_Training)

In [5]:
#Prediction des cibre(salary) depuis les donnees de test Adult_test.csv
Y_Predict_depth = decision_tree_depth.predict(X_Testing)
Y_Predict_node = decision_tree_nodes.predict(X_Testing)

In [6]:
#exportation de l'arbre de decision avec graphviz
names_class = ["+50K", "-50K"]
build_graph = tree.export_graphviz(decision_tree_nodes, out_file=None, 
                     feature_names=names_features,
                     class_names=names_class,
                     filled=True, rounded=True,  
                     special_characters=True) 

In [7]:
graph= graphviz.Source(build_graph)
graph.render("../doc/Q2_Graphe_tree_(max_features)")
graph

In [8]:
#export de l'abre au format texte dans un fichier "Q2_Graphe_tree_(max_features).txt"
r = export_text(decision_tree_nodes,names_features)
fichier = open("../Data/Q2_Graphe_tree_(max_features).txt", "w")
fichier.write(r)
fichier.close()

In [9]:
##__Trace du graphe representant l’erreur de d'entrainement et de prévision pour les deux metaparametre__##

plt.figure()
plt.title("courbes d’apprentissage avec 'max_features'=7")
plt.xlabel("nombre d'instances")
plt.ylabel("Erreur")
plt.grid()

#pour le metaparametre = max_features
train_sizes2, train_scores2, test_scores2=learning_curve(decision_tree_nodes,X_Training,
                           Y_Training,train_sizes=np.arange(1,4447,100), cv=3, shuffle=True)

train_scores_mean2 = np.mean(train_scores2, axis=1)
test_scores_mean2 = np.mean(test_scores2, axis=1)

plt.plot(train_sizes2,1-train_scores_mean2,label="error_train", linestyle="-", color="#d62728")
plt.plot(train_sizes2,1-test_scores_mean2,label="error_test", linestyle="-", color="#2ca02c")


t = 0.2
plot([1300,1300],[0,np.sin(t)], color ='b',  linewidth=1.5, linestyle="--")

plt.text(1300, 1.5, r'Grand ecart entre les courbes:', fontsize=16)
plt.text(1300, 1, r'=>Grande variance', fontsize=16)

plt.legend() 
plt.savefig('../doc/Q2_courbes_apprentissage_avec_max_features=7.pdf')

In [10]:
#matrice de confusion.
All_Error = [["max_depth =3", "max_features =7"],
             [1 - decision_tree_depth.score(X_Training, Y_Training),1 - decision_tree_nodes.score(X_Training, Y_Training)],
             #[1- decision_tree_depth.score(X_Testing, Y_Testing),1- decision_tree_nodes.score(X_Testing, Y_Testing)],
             [1 - decision_tree_depth.score(X_Testing, Y_Testing),1 - decision_tree_nodes.score(X_Testing, Y_Testing)],
            ]


In [11]:
Taille_ligne = 57
espace = 13
print ("comparaison des models des deux Metaparametres:\n\n")

print (" "*espace,"+","-"*(Taille_ligne-espace-1),"+") 
print (" "*espace,"| Metaparametre"," "*29,"|\n"," "*espace, "-"*(Taille_ligne-espace),"+")
print (" "*espace,"| %20s | %20s |" %(All_Error[0][0] ,All_Error[0][1]),"\n+","-"*Taille_ligne,"+" )
print ("| Train_Error | %20s | %20s |" %(All_Error[1][0] ,All_Error[1][1]),"\n+","-"*Taille_ligne,"+")
#print ("| Test_Error | %20s | %20s |" %(All_Error[2][0] ,All_Error[2][1]),"\n+","-"*Taille_ligne,"+" )
print ("| Test_Error  | %20s | %20s |" %(All_Error[2][0] ,All_Error[2][1]),"\n+","-"*Taille_ligne,"+")

comparaison des models des deux Metaparametres:


              + ------------------------------------------- +
              | Metaparametre                               |
               -------------------------------------------- +
              |         max_depth =3 |      max_features =7 | 
+ --------------------------------------------------------- +
| Train_Error |   0.1636935991605456 |                  0.0 | 
+ --------------------------------------------------------- +
| Test_Error  |  0.16299405386498778 |   0.2028681357117873 | 
+ --------------------------------------------------------- +
